# Artificial Intelligence (CC2006) - 2023/2024
## Second assignment: Decision trees

Work by Alexandre Sousa (202206427), Guilherme Oliveira (202204987), Francisco Carqueija (202205113)

In [1]:
import pandas as pd
import logging
from collections import Counter
import re
import random
import math
from Jogo1 import *

# LOAD THE DATA

In [2]:
def remover_colunas_irrelevantes(df, limite_percentual, palavras_chave_id=['id']):
    df_limpo = df.copy()
    colunas_a_remover = []

    for coluna in df.columns:
       
        # Verificação se o nome da coluna contém alguma das palavras chave para ID
        coluna_lower = coluna.lower()
        if any(re.fullmatch(rf'\b{palavra}\b', coluna_lower) for palavra in palavras_chave_id):
            if coluna not in colunas_a_remover:
                colunas_a_remover.append(coluna)
                

    # Remove as colunas identificadas
    df_limpo.drop(colunas_a_remover, axis=1, inplace=True)
    

    return df_limpo

Converte o Data Frame para uma matriz, para a ser mais fácil dentro de atualizar dentro da class Tree e Node

In [3]:
def df_to_data_matrix(df):
    return df.values.tolist()


# ENTROPY AND SPLITS CALCULATIONS

In [4]:
def _count_classes(dataset):
    class_counts = {}
    for data in dataset:
        label = data[-1]
        if label in class_counts:
            class_counts[label] += 1
        else:
            class_counts[label] = 1
    return class_counts

In [5]:
def most_common_class(labels):
    class_counts = {}
    for label in labels:
        if label not in class_counts:
            class_counts[label] = 1
        else:
            class_counts[label] += 1
    return max(class_counts,key = class_counts.get)

In [6]:
def entropy(data_label):
    count_classes = {}
    total = len(data_label)
    entropy = 0

    for value in data_label:
        if value not in count_classes:
            count_classes[value] = 1
        else:
            count_classes[value] += 1
    for value in count_classes.values():
        p = value / total
        entropy += -p * math.log2(p)
    return entropy


In [7]:
def attribute_entropy(data_matrix, attributes):
    entropy_attributes = {}
    for _, val in attributes.items():
        unique_attributes = list(set(row[val] for row in data_matrix))
        entropy_attribute = 0
        for value in unique_attributes:
            subset = []
            for row in data_matrix:
                if row[val] == value:
                    
                    subset.append(row[-1])
            if subset:  # Ensure subset is not empty before calculating its entropy
                subset_entropy = entropy(subset)
                subset_probability = len(subset) / len(data_matrix)
                entropy_attribute += subset_entropy * subset_probability
        entropy_attributes[val] = entropy_attribute
    return entropy_attributes

In [8]:
def information_gain(data_matrix, attributes, entropy_class):
    best_info_gain = -float('inf')
    best_attribute = None
    
    for attribute, index in attributes.items():
        entropy_attr = attribute_entropy(data_matrix, attributes)  # Calculate entropy of current attribute
        gain = entropy_class - entropy_attr[index]  # Calculate information gain
        
        if gain > best_info_gain:
            best_info_gain = gain
            best_attribute = attribute
    
    return best_attribute


In [9]:
def split_info_gain(dataset, label_menor, label_maior):
        parent_entropy = entropy(dataset)
        probabily_menor = len(label_menor) / len(dataset)
        probabily_maior = len(label_maior) / len(dataset)
        entropy_menor = entropy(label_menor)
        entropy_maior = entropy(label_maior)
        value_info_gain = parent_entropy - (probabily_menor * entropy_menor) - (probabily_maior * entropy_maior)
        return value_info_gain

In [10]:
def calculate_best_split(data_matrix, atributes, best_attribute):
    unique_values = list(set([linha[attributes[best_attribute]] for linha in data_matrix]))
    best_split = ''
    best_info_gain = -99999
    
    if len(unique_values) == 1:
        return unique_values[0]
    
    for value in unique_values:
        
        is_bigger_subset = []
        is_lower_subset = []
        
        for linha in data_matrix:
            if float(linha[attributes[best_attribute]]) <= float(value):
                is_bigger_subset.append(linha)
            if float(linha[attributes[best_attribute]]) > float(value):
                is_lower_subset.append(linha)
                    
        labels_menor = [linha[-1] for linha in is_bigger_subset]
        labels_maior = [linha[-1] for linha in is_lower_subset]
        
        info_gains  = split_info_gain([linha[-1] for linha in data_matrix], labels_menor, labels_maior)
        if info_gains > best_info_gain:
            best_info_gain = info_gains
            best_split = value
            
    return best_split

# TREE IMPLEMENTATION


In [11]:
def determine_data_type(values):
    """ Determine if the attribute values are numeric or categorical. """
    try:
        [float(value) for value in values]
        return 'numeric'
    except ValueError:
        return 'categorical'

Here's a class Node designed to represent nodes in a decision tree, with attributes to store the attribute being split on, the class label, whether the node is a leaf, the count of class labels, and its children. It also includes methods for a recursive string representation of the tree.

In [12]:
class Node:
    def __init__(self, attribute=None, label=None, is_leaf=False, count=None):
        self.attribute = attribute
        self.label = label
        self.is_leaf = is_leaf
        self.count = count if count is not None else {}
        self.children = {}

    def recursive(self, node, space):
        result = ""
        if node.is_leaf:
            if isinstance(node.count, dict):
                count_str = " ".join(f"{v}" for _, v in node.count.items())
            else:
                count_str = str(node.count)
            result += f"{space}{node.label}({count_str})\n"
        else:
            # Sort children by converting keys to strings to avoid TypeError between float and str
            sorted_children = sorted(node.children.items(), key=lambda x: str(x[0]))
            for value, child in sorted_children:
                result += f"{space}<{node.attribute}>:\n{space}{value}\n"
                result += self.recursive(child, space + "  ")
        return result

    def __str__(self):
        return self.recursive(self, "")


    



Here's a comprehensive Tree class designed to build a decision tree from a dataset and make predictions for new data. This class uses several helper functions and methods to handle the intricacies of decision tree construction and traversal.


__init__: Initializes the Tree class with the dataset, attributes, and the class label column name. It also computes the class entropy and builds the decision tree.
Building the Decision Tree:

'build_tree': A recursive method to construct the decision tree. It handles both categorical and numeric attributes, determining the best attribute to split on and creating child nodes accordingly.
It stops splitting when all examples have the same class label, no attributes are left, or the maximum depth is reached.


'transform': Applies the decision tree to new data to make predictions. It processes each row and uses transform_tree to navigate through the tree.

'transform_tree': Traverses the tree recursively based on the attribute values in the row, returning the predicted class label when a leaf node is reached.

In [13]:
class Tree:
    def __init__(self, data_matrix, attributes, label_class):
        self.dataset = data_matrix
        self.classe = label_class # nome da coluna da classe
        self.entropy_class = entropy([linha[-1] for linha in data_matrix]) # entropia da classe
        #self.entropy_atrributes = {} # dicionario com a entropia de cada atributo
        self.attribute_to_index = {attr: i for i, attr in enumerate(attributes)}

        self.attributes =   {}
        self.reverse_attributes = {} # exemplo : {1: 'sepallength', 2: 'sepalwidth', 3: 'petallength', 4: 'petalwidth', 5: 'class'}
        for key, position in attributes.items():
            if  position != len(attributes) -1:
                self.reverse_attributes[position] = key
                self.attributes[key] = position

        self.attribute_entropy = attribute_entropy(data_matrix, attributes)
        self.root = self.build_tree(data_matrix, self.attributes) # construir a arvore de decisão

    def build_tree(self, data_matrix, attributes, depth = 0, max_depth = 7):
        
        if max_depth is not None and depth >= max_depth:
             return Node(attribute=None, is_leaf=True, label=most_common_class(labels), count=len(labels))
            
        
        labels = [linha[-1] for linha in data_matrix]  # Classes of examples

        if len(set(labels)) == 1:
            return Node(attribute=None, is_leaf=True, label=labels[0], count=_count_classes(data_matrix))

        if not attributes:
            return Node(attribute=None, is_leaf=True, label=most_common_class(labels), count=len(labels))

        best_attribute = information_gain(data_matrix, attributes, self.entropy_class)
        root = Node(best_attribute)
        val = attributes[best_attribute]
        unique_values = list(set(linha[val] for linha in self.dataset))

        data_type = determine_data_type(unique_values)

        if data_type == 'numeric':
            best_split = calculate_best_split(data_matrix, attributes, best_attribute)
            subset_lower = [linha for linha in data_matrix if float(linha[val]) <= float(best_split)]
            subset_higher = [linha for linha in data_matrix if float(linha[val]) > float(best_split)]
            new_attributes = attributes.copy()
            del new_attributes[best_attribute]
            root.children['<= ' + str(best_split)] = self.build_tree(subset_lower, new_attributes, depth + 1, max_depth)
            root.children['> ' + str(best_split)] = self.build_tree(subset_higher, new_attributes, depth + 1, max_depth)
        else:
            for value in unique_values:
                subset = [linha for linha in data_matrix if linha[val] == value]
                if subset:
                    new_attributes = attributes.copy()
                    del new_attributes[best_attribute]
                    child_node = self.build_tree(subset, new_attributes)
                    root.children[value] = child_node
                else:
                    root.children[value] = Node(attribute=None, is_leaf=True, label=most_common_class(labels), count={value: 0})
        return root
    
    def tranform(self, data):
        if not isinstance(data[0], list):  # Check if data is not already a list of lists
            data = [data]  # Make it a list of lists if it's a single row

        results = []
        for row in data:
            result = self.tranform_tree(self.root, row)
            results.append(result)
        return results

    def tranform_tree(self, tree, row):
        if tree.is_leaf:
            return tree.label

        attribute_index = self.attribute_to_index[tree.attribute]  # Get the index of the attribute from the attribute name
        attribute_value = row[attribute_index]

        for key, subtree in tree.children.items():
            
            if isinstance(key, str) and ' ' in key:  # Check if key is correctly formatted
                split_operator, split_value = key.split(' ', 1)  # Split on first space only
                split_value = float(split_value)
                if (split_operator == '<=' and float(attribute_value) <= split_value) or \
                   (split_operator == '>' and float(attribute_value) > split_value):
                    return self.tranform_tree(subtree, row)
            elif isinstance(key, str):  # Handle categorical attributes directly
                if attribute_value == key:
                    return self.tranform_tree(subtree, row)

        return None  # If no path matches, return None indicating no prediction could be made





    def __str__(self):
        return str(self.root)

# MODEL EVALUATION

Below we have the functions that we used to evaluate our model, k-fold cross validation and leave one out cross validation , The last one  we planned to aplly in smaller datasets like weather_ds and restaurant_ds but the results of this last model were not very promising

To have more accurate evaluations, especially on datasets where the classes are imbalanced we decided to calculate  Balanced accuracy, wich  is the average of the recall (or sensitivity) obtained on each class.

First, for k-fold cross-validation, the data is randomly shuffled and split into k folds. In each iteration, a portion of the data is used as the test set while the remaining data is used to train the model. A decision tree model is trained on the training set, and predictions are made for the test set.

To calculate balanced accuracy, we collect the true labels and the model's predictions for each fold. For each class, we compute the components of the confusion matrix: true positives (TP), false negatives (FN), true negatives (TN), and false positives (FP). Sensitivity (recall)  and specificity are calculatede for each class.  Balanced accuracy is then obtained by averaging the sensitivity and specificity values across all classes.

In [14]:
logging.basicConfig(level=logging.INFO)
logger = logging.getLogger()

def calculate_balanced_accuracy(y_true, y_pred):
    labels = set(y_true)
    true_positives = Counter()
    false_negatives = Counter()
    true_negatives = Counter()
    false_positives = Counter()

    for true_label, pred_label in zip(y_true, y_pred):
        if true_label == pred_label:
            true_positives[true_label] += 1
        else:
            false_negatives[true_label] += 1
            false_positives[pred_label] += 1

    for label in labels:
        true_negatives[label] = sum(true_positives.values()) + sum(false_positives.values()) - true_positives[label] - false_positives[label]

    sensitivity = {label: true_positives[label] / (true_positives[label] + false_negatives[label]) for label in labels}
    specificity = {label: true_negatives[label] / (true_negatives[label] + false_positives[label]) for label in labels}

    balanced_accuracy = (sum(sensitivity.values()) + sum(specificity.values())) / (2 * len(labels))
    return balanced_accuracy

def k_fold_cross_validation(data_matrix, k, attributes, df):
    random.shuffle(data_matrix)
    fold_size = len(data_matrix) // k
    balanced_accuracies = []
    max_balanced_accuracy = 0

    for i in range(k):
        logger.info(f"Processing fold {i+1}/{k}")
        start = i * fold_size
        end = len(data_matrix) if i == k - 1 else start + fold_size
        test_set = data_matrix[start:end]
        train_set = data_matrix[:start] + data_matrix[end:]

        tree = Tree(train_set, attributes, df.columns[-1])
        y_true = []
        y_pred = []

        for row in test_set:
            y_true.append(row[-1])
            prediction = tree.tranform([row[:-1]])
            y_pred.append(prediction[0])

        balanced_accuracy = calculate_balanced_accuracy(y_true, y_pred)
        balanced_accuracies.append(balanced_accuracy)
        logger.info(f"Fold {i+1} balanced accuracy: {balanced_accuracy}")
        if balanced_accuracy > max_balanced_accuracy:
            max_balanced_accuracy = balanced_accuracy

    average_balanced_accuracy = sum(balanced_accuracies) / k
    logger.info(f"Average balanced accuracy: {average_balanced_accuracy}")
    return average_balanced_accuracy, max_balanced_accuracy


In [15]:
import random
from collections import Counter

def leave_one_out_cross_validation(data_matrix, attributes, df):
    random.shuffle(data_matrix)
    y_true = []
    y_pred = []

    for i in range(len(data_matrix)):
        test_set = [data_matrix[i]]
        train_set = data_matrix[:i] + data_matrix[i+1:]

        tree = Tree(train_set, attributes, df.columns[-1])

        for row in test_set:
            y_true.append(row[-1])
            prediction = tree.tranform([row[:-1]])
            y_pred.append(prediction[0])

    balanced_accuracy = calculate_balanced_accuracy(y_true, y_pred)
    return balanced_accuracy



# TESTING

# IRIS DATASET

In [26]:

def df_to_data_matrix(df):
    return df.values.tolist()

# Read the CSV file into a DataFrame
df = pd.read_csv('iris.csv')

# Assuming the class label is in the last column and the ID column is absent in your CSV

data = remover_colunas_irrelevantes(df, 0.90)
attributes = {col: idx for idx, col in enumerate(data.columns[:-1])}
data_matrix_iris = df_to_data_matrix(data)

# Initialize and build the tree
tree = Tree(data_matrix_iris, attributes, df.columns[-1])
print(tree)

<petallength>:
<= 1.9
  Iris-setosa(50)
<petallength>:
> 1.9
  <sepallength>:
  <= 6.1
    <sepalwidth>:
    <= 3.0
      Iris-versicolor(43)
    <sepalwidth>:
    > 3.0
      Iris-versicolor(2)
  <sepallength>:
  > 6.1
    <sepalwidth>:
    <= 2.3
      Iris-versicolor(2)
    <sepalwidth>:
    > 2.3
      Iris-virginica(53)



In [17]:
average_accuracy , _ = k_fold_cross_validation(data_matrix_iris, 3 , attributes,df)
average_accuracy_leave_one_out = leave_one_out_cross_validation(data_matrix_iris, attributes, df)
print( "K- FOLD ACCURACY :" , average_accuracy)
print("LEAVE ONE OUT ACCURACY : " , average_accuracy_leave_one_out)

INFO:root:Processing fold 1/3
INFO:root:Fold 1 balanced accuracy: 0.8416666666666667
INFO:root:Processing fold 2/3
INFO:root:Fold 2 balanced accuracy: 0.8093989338175386
INFO:root:Processing fold 3/3
INFO:root:Fold 3 balanced accuracy: 0.8175005211590577
INFO:root:Average balanced accuracy: 0.8228553738810876


K- FOLD ACCURACY : 0.8228553738810876
LEAVE ONE OUT ACCURACY :  0.861056352354796


# RESTAURANT DATASET

In [18]:
df_restaurant = pd.read_csv('restaurant.csv')


# Assuming the class label is in the last column and the ID column is absent in your CSV

data_restaurant = remover_colunas_irrelevantes(df_restaurant, 0.99)
attributes = {col: idx for idx, col in enumerate(data_restaurant.columns[:-1])}
data_matrix_restaurant = df_to_data_matrix(data_restaurant)


# Initialize and build the tree
tree = Tree(data_matrix_restaurant, attributes, df_restaurant.columns[-1])
print(tree)


<Pat>:
Full
  <Hun>:
  No
    No(2)
  <Hun>:
  Yes
    <Type>:
    Burger
      Yes(1)
    <Type>:
    French
      No(0)
    <Type>:
    Italian
      No(1)
    <Type>:
    Thai
      <Fri>:
      No
        No(1)
      <Fri>:
      Yes
        Yes(1)
<Pat>:
Some
  Yes(4)
<Pat>:
nan
  Yes(0)



In [19]:
_ , max_accuracy = k_fold_cross_validation(data_matrix_restaurant, 2 , attributes, df_restaurant)
print("CROSS VALIDATION ACCURACY : " , max_accuracy)
average_accuracy_leave_one_out = leave_one_out_cross_validation(data_matrix_restaurant, attributes, df_restaurant)
print("LEAVE ONE OUT ACCURACY : " , average_accuracy_leave_one_out)

INFO:root:Processing fold 1/2
INFO:root:Fold 1 balanced accuracy: 0.3375
INFO:root:Processing fold 2/2
INFO:root:Fold 2 balanced accuracy: 0.5375
INFO:root:Average balanced accuracy: 0.4375


CROSS VALIDATION ACCURACY :  0.5375
LEAVE ONE OUT ACCURACY :  0.5691287878787878


# WEATHER DATASET

In [20]:
df_weather = pd.read_csv('weather.csv')

# Assuming the class label is in the last column and the ID column is absent in your CSV

data_weather = remover_colunas_irrelevantes(df_weather, 0.99)
attributes = {col: idx for idx, col in enumerate(data_weather.columns[:-1])}
data_matrix_weather = df_to_data_matrix(data_weather)

# Initialize and build the tree
tree = Tree(data_matrix_weather, attributes, df_weather.columns[-1])
print(tree)

<Temp>:
<= 83
  <Humidity>:
  <= 86
    <Weather>:
    overcast
      yes(3)
    <Weather>:
    rainy
      yes(3)
    <Weather>:
    sunny
      yes(2)
  <Humidity>:
  > 86
    <Weather>:
    overcast
      yes(1)
    <Weather>:
    rainy
      yes(2)
    <Weather>:
    sunny
      no(2)
<Temp>:
> 83
  no(1)



In [21]:
_ , max_accuracy = k_fold_cross_validation(data_matrix_weather, 2 , attributes, df_weather)
print("CROSS VALIDATION ACCURACY : " , max_accuracy)
average_accuracy_leave_one_out = leave_one_out_cross_validation(data_matrix_weather, attributes, df_weather)
print("LEAVE ONE OUT ACCURACY : " , average_accuracy_leave_one_out)

INFO:root:Processing fold 1/2
INFO:root:Fold 1 balanced accuracy: 0.4666666666666667
INFO:root:Processing fold 2/2
INFO:root:Fold 2 balanced accuracy: 0.5375
INFO:root:Average balanced accuracy: 0.5020833333333333


CROSS VALIDATION ACCURACY :  0.5375
LEAVE ONE OUT ACCURACY :  0.46495726495726497


#  Connect4 Dataset

In [22]:

df_connect4 = pd.read_csv('connect4.csv')

# Assuming the class label is in the last column and the ID column is absent in your CSV

data_connect4 = remover_colunas_irrelevantes(df_connect4, 0.99)
attributes = {col: idx for idx, col in enumerate(data_connect4.columns[:-1])}
data_matrix_connect4= df_to_data_matrix(data_connect4)

# Initialize and build the tree 
tree_connect4 = Tree(data_matrix_connect4, attributes, df_connect4.columns[-1])
print(tree_connect4) 



<b>:
b
  <b.28>:
  b
    <x.2>:
    b
      <o.1>:
      b
        <b.12>:
        b
          <o>:
          b
            <b.6>:
            b
              <b.22>:
              b
                win(4)
              <b.22>:
              o
                <b.24>:
                b
                  win(16)
                <b.24>:
                o
                  <b.27>:
                  b
                    <b.19>:
                    b
                      <b.26>:
                      b
                        win(6)
                      <b.26>:
                      o
                        <x>:
                        b
                          win(0)
                        <x>:
                        o
                          win(1)
                        <x>:
                        x
                          draw(1)
                      <b.26>:
                      x
                        win(1)
                    <b.19>:
                    o
           

In [23]:
average_accuracy , _ = k_fold_cross_validation(data_matrix_connect4, 2, attributes, df_weather)
print( "K- FOLD ACCURACY :" , average_accuracy)

INFO:root:Processing fold 1/2
INFO:root:Fold 1 balanced accuracy: 0.7151370221333254
INFO:root:Processing fold 2/2
INFO:root:Fold 2 balanced accuracy: 0.7241351153290214
INFO:root:Average balanced accuracy: 0.7196360687311734


K- FOLD ACCURACY : 0.7196360687311734


# New Inputs Classification

In [27]:
def classify_instance(line, tree):
    
    values = line.split(',')
    
    # Remove leading/trailing whitespaces from attribute values
    values = [value.strip() for value in values]
    
    classification = tree.tranform(values)
    
    return classification


In [28]:
tree = Tree(data_matrix_iris, attributes, df.columns[-1])
print(tree)

<petallength>:
<= 1.9
  Iris-setosa(50)
<petallength>:
> 1.9
  <sepallength>:
  <= 6.1
    <sepalwidth>:
    <= 3.0
      Iris-versicolor(43)
    <sepalwidth>:
    > 3.0
      Iris-versicolor(2)
  <sepallength>:
  > 6.1
    <sepalwidth>:
    <= 2.3
      Iris-versicolor(2)
    <sepalwidth>:
    > 2.3
      Iris-virginica(53)



In [ ]:
# EXAMPLE

line = "5.1,3.5,1.4,0.2"  
classification = classify_instance(line, tree)
print("Classification:", classification) 

Classification: ['Iris-setosa']


 # New Data Set predictions

In [ ]:
def prever_dataset(data_matrix, tree):
    y_pred = []
    for row in data_matrix:
        
        prediction = tree.tranform([row])
        y_pred.append(prediction[0])

    return y_pred

In [ ]:
df = pd.read_csv('teste.csv')

data_matrix= df_to_data_matrix(data_connect4)

y_pred = prever_dataset(data_matrix,tree)

print(y_pred)


FileNotFoundError: [Errno 2] No such file or directory: 'teste.csv'

# Connect4 move prediction

This function transforms the board from the game to a line that is readable by the Decision Tree

In [29]:
def transform_connect_four_to_dataset(state):
    resp = ""
    linha = 0
    coluna = 0
    for i in range(42):  # Supondo que o tabuleiro seja de 7 colunas e 6 linhas
        if linha == 6:
            linha = 0
            coluna += 1
        
        # Obtem o valor corrente sem alterar o estado original
        valor_atual = state[5-linha][coluna]
        
        # Verifica o valor e atribui o correspondente
        if valor_atual == 0:  # Usando valores numéricos diretos, sem aspas
            char = 'b'
        elif valor_atual == 1:
            char = 'x'
        elif valor_atual == 2:
            char = 'o'
        else:
            char = str(valor_atual)  # Conversão explícita para string, para segurança
        
        resp += char + ","
        linha += 1
        
    resp = resp.rstrip(',')
    return resp


In [30]:
def predict_move_tree(state,tree,player):
    heuristica = Heuristica_AStar()
    sucessores = heuristica.generate_sucessors(state,player)
    
    movimentos_ganhos = []
    movimentos_empatados = []
    
    for i in range(len(sucessores)): 
      
        
        resp = transform_connect_four_to_dataset(sucessores[i][0])
        
        previsao = classify_instance(resp,tree)
        
        
        if previsao == "win":
            movimentos_ganhos.append(sucessores[i][1])
        if previsao == "draw":
            movimentos_empatados.append(sucessores[i][1])
    if movimentos_ganhos == []:
        if movimentos_empatados != []: 
            state.drop_pieces(player, random_choice(movimentos_empatados))
        else: 
            possible_moves = [col for col in range(7) if state.valid_col(col)]
            if possible_moves:
                random_move = random.choice(possible_moves)  # Escolhe um movimento possível aleatório
                state.drop_pieces(player, random_move)
    else: 
            possible_moves = [col for col in range(7) if state.valid_col(col)]
            if possible_moves:
                random_move = random.choice(possible_moves)  # Escolhe um movimento possível aleatório
                state.drop_pieces(player, random_move)


        
    

Implementation of the Connect 4, to see how the decision tree plaies agains a Player, or A*.

In [32]:
state = Board()
print(state.board)

print("1. Decision Tree vs Player")
print("2. Decision Tree vs A*")

game_mode = int(input("Choose Game Mode (1 ou 2): "))
heuristica = Heuristica_AStar()

while not state.is_full():
    
    
    if state.turn == 0:
        predict_move_tree(state,tree_connect4, state.turn +1)
        print(state.board)
        if state.win(state.turn + 1):
            print(f"Decision Tree wins!")
            break
    else: 
        if game_mode == 1:
            n=int(input(f"Player 2 turn: "))
            state.drop_pieces(2, n)
            print(state.board)
        else: 
            best_move = heuristica.astar_algorithm(state,state.turn + 1)
            state.drop_pieces(2, n)
            
        if state.win(state.turn + 1):
            print(f"CPU {game_mode} wins!")
            break
        
    state.turn = 1 - state.turn  
if state.is_full(): 
    print("Draw")
    

[[0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0.]]
1. Decision Tree vs Player
2. Decision Tree vs A*
[[0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 1. 0. 0.]]
[[0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 2. 0. 1. 0. 0.]]
[[0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 2. 0. 1. 0. 1.]]
[[0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 2. 0. 0. 0. 0.]
 [0. 0. 2. 0. 1. 0. 1.]]
[[0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 2. 0. 0. 0. 0.]
 [0. 1. 2. 0. 1. 0. 1.]]
[[0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 